In [1]:
import xarray as xr
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from oggm.utils import file_downloader, mkdir
from matplotlib.backends.backend_pdf import PdfPages

In [2]:
periods = ['1851-1870', '1901-1920', '1951-1970', '1995-2014']

In [3]:
val_per_reg = dict()

for reg in range(1, 20):
    reg = f'RGI{reg:02d}'
    df = pd.DataFrame()
    for period in periods:
        try:
            with xr.open_dataset(f'clean/{reg}/gfdl-esm4_historical_{period}.nc') as ds:
                df[period] = ds.volume.load().sum(dim='rgi_id').to_series()
        except:
            continue
    if len(df) > 0:
        val_per_reg[reg] = df

In [4]:
with PdfPages('plots/historical_region_ts.pdf') as pdf:
    for reg in val_per_reg.keys():
        df = val_per_reg[reg]
        plt.figure(figsize=(8, 6))
        df.plot();
        plt.title(reg); plt.ylabel('Volume [km3]')
        pdf.savefig()
        plt.close();

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

...

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

### Stop criterions - SMB based

In [26]:
# Criterion 1 - at least N years with zero volume in W years
window_size_zero_vol = 20
n_years_zero = 5

# Criterion 2 - average SMB during W years less than threshold
window_size_smb = 20
threshold_smb = 100  # kg m2 yr-1
window_size_smb = 100
threshold_smb = 0.01  # m i.e. yr-1

val_per_reg_stop = dict()
stop_statistics_per_reg = dict()

for reg in range(1, 20):
# for reg in [1]:
    reg = f'RGI{reg:02d}'
    print(reg)
    df = pd.DataFrame()
    df_stats = pd.DataFrame()
    for period in periods:
        try:
            with xr.open_dataset(f'clean/{reg}/gfdl-esm4_historical_{period}.nc') as ds:
                ds = ds.load()
        except:
            continue
        
        # Get the data
        df_vol_orig = pd.DataFrame(index=ds.time, columns=ds.rgi_id, data=ds.volume.data.copy())
        df_vol = pd.DataFrame(index=ds.time, columns=ds.rgi_id, data=ds.volume.data.copy())
        df_area = pd.DataFrame(index=ds.time, columns=ds.rgi_id, data=ds.area.data)  
        
        df_stats.loc['no_stop', period] = (~ df_vol.isnull()).sum().mean()
        
        # Criterion 1
        df0 = (df_vol <= 0).rolling(window=window_size_zero_vol, min_periods=window_size_zero_vol).sum()
        first_occu = (df0 >= n_years_zero).idxmax()
        for i, e in enumerate(first_occu):
            if e > 0:
                df_vol.values[int(e):, i] = np.NaN
        # stats
        df_stats.loc['after_vol0', period] = (~ df_vol.isnull()).sum().mean()
        
        # Criterion 2
        smb = (df_vol.loc[1:].values - df_vol.iloc[:-1]) / df_area.iloc[:-1].values
        smb[df_area.iloc[:-1] < 1] = 0
        first_occu = (smb.rolling(window_size_smb, min_periods=window_size_smb).mean().abs() <= threshold_smb).idxmax()
        for i, e in enumerate(first_occu):
            if e > (window_size_smb - 1):
                df_vol.values[int(e):, i] = np.NaN
        # stats
        df_stats.loc['after_smb', period] = (~ df_vol.isnull()).sum().mean()
        
        # Write
        df_vol = df_vol.fillna(method='ffill')
        df[period] = df_vol.sum(axis=1)
        
    if len(df) > 0:
        val_per_reg_stop[reg] = df
        stop_statistics_per_reg[reg] = df_stats

RGI01
RGI02
RGI03
RGI04
RGI05
RGI06
RGI07
RGI08
RGI09
RGI10
RGI11
RGI12
RGI13
RGI14
RGI15
RGI16
RGI17
RGI18
RGI19


In [27]:
with PdfPages('plots/historical_region_ts_stop_001mice.pdf') as pdf:
    for reg in val_per_reg.keys():
        df = val_per_reg[reg]
        plt.figure(figsize=(8, 6))

        df = val_per_reg[reg]
        df_stop = val_per_reg_stop[reg]

        df = df / df.iloc[0]
        df_stop = df_stop / df_stop.iloc[0]

        f, ax = plt.subplots()
        df.plot(ax=ax, color=['C0', 'C1', 'C2', 'C3'], alpha=0.5);
        df_stop.plot(ax=ax, linestyle='--', color=['C0', 'C1', 'C2', 'C3'], legend=False);
        plt.title(reg + ' (dash=stop). Stop crit 2 (SMB based, 100 yr period)'); plt.ylabel('Volume [% RGI]')
        pdf.savefig()
        plt.close();

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

...

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

In [28]:
for reg in val_per_reg.keys():
    print(reg, stop_statistics_per_reg[reg].loc['after_smb'].max())

RGI01 433.6428014697695
RGI02 465.3676979783313
RGI03 626.6901041666666
RGI04 465.41903940178315
RGI05 506.13146042112373
RGI06 566.2607076350093
RGI07 507.85645933014354
RGI08 514.5727554179566
RGI09 793.9945175438596
RGI10 389.7984705353126
RGI11 381.11841432225066
RGI12 411.94455445544554
RGI13 439.730407035567
RGI15 412.73577363223075
RGI16 771.7819433817904
RGI18 876.2830296127563
RGI19 459.05501130369254


In [7]:
for reg in val_per_reg.keys():
    print(reg, stop_statistics_per_reg[reg].loc['after_smb'].max())

RGI01 599.5719481869131
RGI02 596.3714955880711
RGI03 699.4360795454545
RGI04 505.41084268047166
RGI05 676.4003490597905
RGI06 660.3463687150838
RGI07 657.4203691045797
RGI08 630.590092879257
RGI09 872.0230263157895
RGI10 480.56567701304544
RGI11 461.6480818414322
RGI12 585.3320132013201
RGI13 620.8455327262822
RGI15 602.2393792130428
RGI16 1214.0237184391738
RGI18 1135.0700455580866
RGI19 546.6684250188395


In [8]:
stop_statistics_per_reg['RGI09']

1851-1870    1901-1920    1951-1970    1995-2014
no_stop     5001.000000  5001.000000  5001.000000  5001.000000
after_vol0  3763.097588  3504.607456  3343.237939  3603.347588
after_smb    872.023026   742.748904   735.100877   801.257675

## Stop criterion - volume based 

In [16]:
# Criterion 1 - at least N years with zero volume in W years
window_size_zero_vol = 20
n_years_zero = 5

# Criterion 2 - 1% volume change
window_size_vol = 100
perc_vol = 0.001

val_per_reg_stop = dict()
stop_statistics_per_reg = dict()

for reg in range(1, 20):
# for reg in [1]:
    reg = f'RGI{reg:02d}'
    print(reg)
    df = pd.DataFrame()
    df_stats = pd.DataFrame()
    for period in periods:
        try:
            with xr.open_dataset(f'clean/{reg}/gfdl-esm4_historical_{period}.nc') as ds:
                ds = ds.load()
        except:
            continue
        
        # Get the data
        df_vol_orig = pd.DataFrame(index=ds.time, columns=ds.rgi_id, data=ds.volume.data.copy())
        df_vol = pd.DataFrame(index=ds.time, columns=ds.rgi_id, data=ds.volume.data.copy())
        df_area = pd.DataFrame(index=ds.time, columns=ds.rgi_id, data=ds.area.data)  
        
        df_stats.loc['no_stop', period] = (~ df_vol.isnull()).sum().mean()
        
        # Criterion 1
        df0 = (df_vol <= 0).rolling(window=window_size_zero_vol, min_periods=window_size_zero_vol).sum()
        first_occu = (df0 >= n_years_zero).idxmax()
        for i, e in enumerate(first_occu):
            if e > 0:
                df_vol.values[int(e):, i] = np.NaN
        # stats
        df_stats.loc['after_vol0', period] = (~ df_vol.isnull()).sum().mean()
        
        # Criterion 2
        vol_avg = df_vol.rolling(window_size_vol, min_periods=window_size_vol).mean()
        dif_vol = (vol_avg.iloc[window_size_vol:] - vol_avg.iloc[window_size_vol-40:-40].values).abs()
        to_stop = dif_vol < (perc_vol * df_vol.iloc[0])
        first_occu = to_stop.idxmax()
        for i, e in enumerate(first_occu):
            if e > (window_size_vol - 1):
                df_vol.values[int(e):, i] = np.NaN
        # stats
        df_stats.loc['after_smb', period] = (~ df_vol.isnull()).sum().mean()
        
        # Write
        df_vol = df_vol.fillna(method='ffill')
        df[period] = df_vol.sum(axis=1)
        
    if len(df) > 0:
        val_per_reg_stop[reg] = df
        stop_statistics_per_reg[reg] = df_stats

RGI01
RGI02
RGI03
RGI04
RGI05
RGI06
RGI07
RGI08
RGI09
RGI10
RGI11
RGI12
RGI13
RGI14
RGI15
RGI16
RGI17
RGI18
RGI19


In [20]:
with PdfPages('plots/historical_region_ts_stop5.pdf') as pdf:
    for reg in val_per_reg_stop.keys():
        df = val_per_reg[reg]
        plt.figure(figsize=(8, 6))

        df = val_per_reg[reg]
        df_stop = val_per_reg_stop[reg]

        df = df / df.iloc[0]
        df_stop = df_stop / df_stop.iloc[0]

        f, ax = plt.subplots()
        df.plot(ax=ax, color=['C0', 'C1', 'C2', 'C3'], alpha=0.5);
        df_stop.plot(ax=ax, linestyle='--', color=['C0', 'C1', 'C2', 'C3'], legend=False);
        plt.title(reg + ' (dash=stop). Stop crit 5 ($\Delta$ V < 0.1% V$_{RGI}$)'); plt.ylabel('Volume [% RGI]')
        pdf.savefig()
        plt.close();

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

...

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

In [18]:
for reg in val_per_reg.keys():
    print(reg, stop_statistics_per_reg[reg].loc['after_smb'].max())

RGI01 249.39011988271537
RGI02 373.78068803752933
RGI03 456.3560606060606
RGI04 364.50460166810467
RGI05 361.4299628420223
RGI06 446.5623836126629
RGI07 387.4941900205058
RGI08 465.2136222910217
RGI09 618.3958333333334
RGI10 311.982905982906
RGI11 237.75805626598466
RGI12 275.2660066006601
RGI13 396.9437893999533
RGI15 258.93776453989653
RGI16 425.08110175975514
RGI18 631.8174829157175
RGI19 447.8319517709118


In [21]:
stop_statistics_per_reg['RGI09']

1851-1870    1901-1920    1951-1970    1995-2014
no_stop     5001.000000  5001.000000  5001.000000  5001.000000
after_vol0  3763.097588  3504.607456  3343.237939  3603.347588
after_smb    618.395833   536.737939   498.768640   591.904605

## Stop criterion - volume based 2

In [22]:
# Criterion 1 - at least N years with zero volume in W years
window_size_zero_vol = 20
n_years_zero = 5

# Criterion 2 - 1% volume change
window_size_vol = 100
perc_vol = 0.001

val_per_reg_stop = dict()
stop_statistics_per_reg = dict()

for reg in range(1, 20):
# for reg in [1]:
    reg = f'RGI{reg:02d}'
    print(reg)
    df = pd.DataFrame()
    df_stats = pd.DataFrame()
    for period in periods:
        try:
            with xr.open_dataset(f'clean/{reg}/gfdl-esm4_historical_{period}.nc') as ds:
                ds = ds.load()
        except:
            continue
        
        # Get the data
        df_vol_orig = pd.DataFrame(index=ds.time, columns=ds.rgi_id, data=ds.volume.data.copy())
        df_vol = pd.DataFrame(index=ds.time, columns=ds.rgi_id, data=ds.volume.data.copy())
        df_area = pd.DataFrame(index=ds.time, columns=ds.rgi_id, data=ds.area.data)  
        
        df_stats.loc['no_stop', period] = (~ df_vol.isnull()).sum().mean()
        
        # Criterion 1
        df0 = (df_vol <= 0).rolling(window=window_size_zero_vol, min_periods=window_size_zero_vol).sum()
        first_occu = (df0 >= n_years_zero).idxmax()
        for i, e in enumerate(first_occu):
            if e > 0:
                df_vol.values[int(e):, i] = np.NaN
        # stats
        df_stats.loc['after_vol0', period] = (~ df_vol.isnull()).sum().mean()
        
        # Criterion 2
        vol_avg = df_vol.rolling(window_size_vol, min_periods=window_size_vol).mean()
        dif_vol = (vol_avg.iloc[window_size_vol:] - vol_avg.iloc[window_size_vol-40:-40].values).abs() / vol_avg.iloc[window_size_vol:].values
        to_stop = dif_vol < perc_vol
        first_occu = to_stop.idxmax()
        for i, e in enumerate(first_occu):
            if e > (window_size_vol - 1):
                df_vol.values[int(e):, i] = np.NaN
        # stats
        df_stats.loc['after_smb', period] = (~ df_vol.isnull()).sum().mean()
        
        # Write
        df_vol = df_vol.fillna(method='ffill')
        df[period] = df_vol.sum(axis=1)
        
    if len(df) > 0:
        val_per_reg_stop[reg] = df
        stop_statistics_per_reg[reg] = df_stats

RGI01
RGI02
RGI03
RGI04
RGI05
RGI06
RGI07
RGI08
RGI09
RGI10
RGI11
RGI12
RGI13
RGI14
RGI15
RGI16
RGI17
RGI18
RGI19


In [14]:
with PdfPages('plots/historical_region_ts_stop4.pdf') as pdf:
    for reg in val_per_reg_stop.keys():
        df = val_per_reg[reg]
        plt.figure(figsize=(8, 6))

        df = val_per_reg[reg]
        df_stop = val_per_reg_stop[reg]

        df = df / df.iloc[0]
        df_stop = df_stop / df_stop.iloc[0]

        f, ax = plt.subplots()
        df.plot(ax=ax, color=['C0', 'C1', 'C2', 'C3'], alpha=0.5);
        df_stop.plot(ax=ax, linestyle='--', color=['C0', 'C1', 'C2', 'C3'], legend=False);
        plt.title(reg + ' (dash=stop). Stop crit 3 ($\Delta$ V < 1% V$_{1}$)'); plt.ylabel('Volume [% RGI]')
        pdf.savefig()
        plt.close();

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

...

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

<Figure size 576x432 with 0 Axes>

In [15]:
for reg in val_per_reg.keys():
    print(reg, stop_statistics_per_reg[reg].loc['after_smb'].max())

RGI01 163.28374716995137
RGI02 195.92845973416732
RGI03 349.3394886363636
RGI04 295.76402070750646
RGI05 266.7824006305596
RGI06 324.4823091247672
RGI07 315.39576213260426
RGI08 309.77647058823527
RGI09 420.3519736842105
RGI10 218.87786774628879
RGI11 141.87826086956522
RGI12 194.2924092409241
RGI13 275.56393493657094
RGI15 156.1628781940743
RGI16 123.2628156082632
RGI18 153.18023917995444
RGI19 278.46571213263


In [12]:
stop_statistics_per_reg['RGI09']

1851-1870    1901-1920    1951-1970    1995-2014
no_stop     5001.000000  5001.000000  5001.000000  5001.000000
after_vol0  3763.097588  3504.607456  3343.237939  3603.347588
after_smb    402.768640   377.073465   351.972588   397.868421

In [ ]:
to_stop['RGI60-01.00002']

In [ ]:
(~ df_vol.isnull()).sum().mean()

In [ ]:
.plot();
df_vol['RGI60-19.00078'].plot();

In [ ]:
first_occu.loc[first_occu > 19]

In [ ]:
df_vol.iloc[0].isnull().sum()

In [ ]:
df_vol.iloc[0].sum(), df_orig.iloc[0].sum()

In [ ]:
valid_ids_per_reg = dict()
area_stats = pd.DataFrame()
for reg in range(1, 20):
    reg = f'RGI{reg:02d}'
    if reg not in val_per_reg:
        continue
    df = val_per_reg[reg]
    val_ids = df.loc[df.all(axis=1)].index
    valid_ids_per_reg[reg] = val_ids
    
    # Stats
    df_rgi_reg = df_rgi.loc[df_rgi['O1Region'] == reg[-2:]]
    area_stats.loc[reg, 'all'] = 1 - df_rgi_reg.loc[val_ids].Area.sum() / df_rgi_reg.Area.sum()
    
    # Stats per period
    for period in periods:
        val_ids = df.loc[df[period]].index
        area_stats.loc[reg, period] = 1 - df_rgi_reg.loc[val_ids].Area.sum() / df_rgi_reg.Area.sum()

In [ ]:
area_stats

In [ ]:
for reg in range(1, 20):
    reg = f'RGI{reg:02d}'
    df = pd.DataFrame()
    for period in periods:
        odir = f'clean/{reg}/'
        try:
            with xr.open_dataset(f'output/{reg}/gfdl-esm4_historical_{period}.nc') as ds:
                val_ids = valid_ids_per_reg[reg]
                ds = ds[['volume', 'area']].load().sel(rgi_id=val_ids)
                mkdir(odir)
                ds.to_netcdf(f'{odir}/gfdl-esm4_historical_{period}.nc')
        except FileNotFoundError:
            continue